# DonorsChoose

<p>
DonorsChoose.org receives hundreds of thousands of project proposals each year for classroom projects in need of funding. Right now, a large number of volunteers is needed to manually screen each submission before it's approved to be posted on the DonorsChoose.org website.
</p>
<p>
    Next year, DonorsChoose.org expects to receive close to 500,000 project proposals. As a result, there are three main problems they need to solve:
<ul>
<li>
    How to scale current manual processes and resources to screen 500,000 projects so that they can be posted as quickly and as efficiently as possible</li>
    <li>How to increase the consistency of project vetting across different volunteers to improve the experience for teachers</li>
    <li>How to focus volunteer time on the applications that need the most assistance</li>
    </ul>
</p>    
<p>
The goal of the competition is to predict whether or not a DonorsChoose.org project proposal submitted by a teacher will be approved, using the text of project descriptions as well as additional metadata about the project, teacher, and school. DonorsChoose.org can then use this information to identify projects most likely to need further review before approval.
</p>

## About the DonorsChoose Data Set

The `train.csv` data set provided by DonorsChoose contains the following features:

Feature | Description 
----------|---------------
**`project_id`** | A unique identifier for the proposed project. **Example:** `p036502`   
**`project_title`**    | Title of the project. **Examples:**<br><ul><li><code>Art Will Make You Happy!</code></li><li><code>First Grade Fun</code></li></ul> 
**`project_grade_category`** | Grade level of students for which the project is targeted. One of the following enumerated values: <br/><ul><li><code>Grades PreK-2</code></li><li><code>Grades 3-5</code></li><li><code>Grades 6-8</code></li><li><code>Grades 9-12</code></li></ul>  
 **`project_subject_categories`** | One or more (comma-separated) subject categories for the project from the following enumerated list of values:  <br/><ul><li><code>Applied Learning</code></li><li><code>Care &amp; Hunger</code></li><li><code>Health &amp; Sports</code></li><li><code>History &amp; Civics</code></li><li><code>Literacy &amp; Language</code></li><li><code>Math &amp; Science</code></li><li><code>Music &amp; The Arts</code></li><li><code>Special Needs</code></li><li><code>Warmth</code></li></ul><br/> **Examples:** <br/><ul><li><code>Music &amp; The Arts</code></li><li><code>Literacy &amp; Language, Math &amp; Science</code></li>  
  **`school_state`** | State where school is located ([Two-letter U.S. postal code](https://en.wikipedia.org/wiki/List_of_U.S._state_abbreviations#Postal_codes)). **Example:** `WY`
**`project_subject_subcategories`** | One or more (comma-separated) subject subcategories for the project. **Examples:** <br/><ul><li><code>Literacy</code></li><li><code>Literature &amp; Writing, Social Sciences</code></li></ul> 
**`project_resource_summary`** | An explanation of the resources needed for the project. **Example:** <br/><ul><li><code>My students need hands on literacy materials to manage sensory needs!</code</li></ul> 
**`project_essay_1`**    | First application essay<sup>*</sup>  
**`project_essay_2`**    | Second application essay<sup>*</sup> 
**`project_essay_3`**    | Third application essay<sup>*</sup> 
**`project_essay_4`**    | Fourth application essay<sup>*</sup> 
**`project_submitted_datetime`** | Datetime when project application was submitted. **Example:** `2016-04-28 12:43:56.245`   
**`teacher_id`** | A unique identifier for the teacher of the proposed project. **Example:** `bdf8baa8fedef6bfeec7ae4ff1c15c56`  
**`teacher_prefix`** | Teacher's title. One of the following enumerated values: <br/><ul><li><code>nan</code></li><li><code>Dr.</code></li><li><code>Mr.</code></li><li><code>Mrs.</code></li><li><code>Ms.</code></li><li><code>Teacher.</code></li></ul>  
**`teacher_number_of_previously_posted_projects`** | Number of project applications previously submitted by the same teacher. **Example:** `2` 

<sup>*</sup> See the section <b>Notes on the Essay Data</b> for more details about these features.

Additionally, the `resources.csv` data set provides more data about the resources required for each project. Each line in this file represents a resource required by a project:

Feature | Description 
----------|---------------
**`id`** | A `project_id` value from the `train.csv` file.  **Example:** `p036502`   
**`description`** | Desciption of the resource. **Example:** `Tenor Saxophone Reeds, Box of 25`   
**`quantity`** | Quantity of the resource required. **Example:** `3`   
**`price`** | Price of the resource required. **Example:** `9.95`   

**Note:** Many projects require multiple resources. The `id` value corresponds to a `project_id` in train.csv, so you use it as a key to retrieve all resources needed for a project:

The data set contains the following label (the value you will attempt to predict):

Label | Description
----------|---------------
`project_is_approved` | A binary flag indicating whether DonorsChoose approved the project. A value of `0` indicates the project was not approved, and a value of `1` indicates the project was approved.

### Notes on the Essay Data

<ul>
Prior to May 17, 2016, the prompts for the essays were as follows:
<li>__project_essay_1:__ "Introduce us to your classroom"</li>
<li>__project_essay_2:__ "Tell us more about your students"</li>
<li>__project_essay_3:__ "Describe how your students will use the materials you're requesting"</li>
<li>__project_essay_3:__ "Close by sharing why your project will make a difference"</li>
</ul>


<ul>
Starting on May 17, 2016, the number of essays was reduced from 4 to 2, and the prompts for the first 2 essays were changed to the following:<br>
<li>__project_essay_1:__ "Describe your students: What makes your students special? Specific details about their background, your neighborhood, and your school are all helpful."</li>
<li>__project_essay_2:__ "About your project: How will these materials make a difference in your students' learning and improve their school lives?"</li>
<br>For all projects with project_submitted_datetime of 2016-05-17 and later, the values of project_essay_3 and project_essay_4 will be NaN.
</ul>


In [1]:
%matplotlib inline
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer


import re
# Tutorial about Python regular expressions: https://pymotw.com/2/re/

from nltk.corpus import stopwords
import pickle

from tqdm import tqdm
import os

## 1. Reading Data

In [2]:
project_data = pd.read_csv('train_data.csv')
print('project data shape:', project_data.shape)
project_data.head(3)

project data shape: (109248, 17)


Unnamed: 0       id                        teacher_id teacher_prefix  \
0      160221  p253737  c90749f5d961ff158d4b4d1e7dc665fc           Mrs.   
1      140945  p258326  897464ce9ddc600bced1151f324dd63a            Mr.   
2       21895  p182444  3465aaf82da834c0582ebd0ef8040ca0            Ms.   

  school_state project_submitted_datetime project_grade_category  \
0           IN        2016-12-05 13:43:57          Grades PreK-2   
1           FL        2016-10-25 09:22:10             Grades 6-8   
2           AZ        2016-08-31 12:03:56             Grades 6-8   

          project_subject_categories     project_subject_subcategories  \
0                Literacy & Language                     ESL, Literacy   
1  History & Civics, Health & Sports  Civics & Government, Team Sports   
2                    Health & Sports    Health & Wellness, Team Sports   

                                       project_title  \
0   Educational Support for English Learners at Home   
1              Wanted: Projector for Hungry Learners   
2  Soccer Equipment for AWESOME Middle School Stu...   

                                     project_essay_1  \
0  My students are English learners that are work...   
1  Our students arrive to our school eager to lea...   
2  \r\n\"True champions aren't always the ones th...   

                                     project_essay_2 project_essay_3  \
0  \"The limits of your language are the limits o...             NaN   
1  The projector we need for our school is very c...             NaN   
2  The students on the campus come to school know...             NaN   

  project_essay_4                           project_resource_summary  \
0             NaN  My students need opportunities to practice beg...   
1             NaN  My students need a projector to help with view...   
2             NaN  My students need shine guards, athletic socks,...   

   teacher_number_of_previously_posted_projects  project_is_approved  
0                                             0                    0  
1                                             7                    1  
2                                             1                    0

In [3]:
resource_data = pd.read_csv('resources.csv')
print('resource data shape:', resource_data.shape)
resource_data.head()

resource data shape: (1541272, 4)


id                                        description  quantity  \
0  p233245  LC652 - Lakeshore Double-Space Mobile Drying Rack         1   
1  p069063        Bouncy Bands for Desks (Blue support pipes)         3   
2  p069063  Cory Stories: A Kid's Book About Living With Adhd         1   
3  p069063  Dixon Ticonderoga Wood-Cased #2 HB Pencils, Bo...         2   
4  p069063  EDUCATIONAL INSIGHTS FLUORESCENT LIGHT FILTERS...         3   

    price  
0  149.00  
1   14.95  
2    8.45  
3   13.59  
4   24.95

# 2. Preprocessing Categorical Features: project_grade_category

In [4]:
project_data['project_grade_category'].value_counts()

Grades PreK-2    44225
Grades 3-5       37137
Grades 6-8       16923
Grades 9-12      10963
Name: project_grade_category, dtype: int64

we need to remove the spaces, replace the '-' with '_' and convert all the letters to small

In [5]:
# https://stackoverflow.com/questions/36383821/pandas-dataframe-apply-function-to-column-strings-based-on-other-column-value
project_data['project_grade_category'] = project_data['project_grade_category'].str.lower().str.replace(' ','_').str.replace('-','_')
project_data['project_grade_category'].value_counts()

grades_prek_2    44225
grades_3_5       37137
grades_6_8       16923
grades_9_12      10963
Name: project_grade_category, dtype: int64

# 3. Preprocessing Categorical Features: project_subject_categories

In [6]:
project_data['project_subject_categories'].value_counts()

Literacy & Language                           23655
Math & Science                                17072
Literacy & Language, Math & Science           14636
Health & Sports                               10177
Music & The Arts                               5180
Special Needs                                  4226
Literacy & Language, Special Needs             3961
Applied Learning                               3771
Math & Science, Literacy & Language            2289
Applied Learning, Literacy & Language          2191
History & Civics                               1851
Math & Science, Special Needs                  1840
Literacy & Language, Music & The Arts          1757
Math & Science, Music & The Arts               1642
Applied Learning, Special Needs                1467
History & Civics, Literacy & Language          1421
Health & Sports, Special Needs                 1391
Warmth, Care & Hunger                          1309
Math & Science, Applied Learning               1220
Applied Lear

>remove spaces, 'the' <br>
replace '&' with '\_', and ',' with '_'

In [7]:
project_data['project_subject_categories'] = project_data['project_subject_categories'].str.replace(' The ','')
project_data['project_subject_categories'] = project_data['project_subject_categories'].str.replace(' ','')
project_data['project_subject_categories'] = project_data['project_subject_categories'].str.replace('&','_')
project_data['project_subject_categories'] = project_data['project_subject_categories'].str.replace(',','_')
project_data['project_subject_categories'] = project_data['project_subject_categories'].str.lower()
project_data['project_subject_categories'].value_counts()

literacy_language                       23655
math_science                            17072
literacy_language_math_science          14636
health_sports                           10177
music_arts                               5180
specialneeds                             4226
literacy_language_specialneeds           3961
appliedlearning                          3771
math_science_literacy_language           2289
appliedlearning_literacy_language        2191
history_civics                           1851
math_science_specialneeds                1840
literacy_language_music_arts             1757
math_science_music_arts                  1642
appliedlearning_specialneeds             1467
history_civics_literacy_language         1421
health_sports_specialneeds               1391
warmth_care_hunger                       1309
math_science_appliedlearning             1220
appliedlearning_math_science             1052
literacy_language_history_civics          809
health_sports_literacy_language   

# 4. Preprocessing Categorical Features: teacher_prefix

In [8]:
project_data['teacher_prefix'].value_counts()

Mrs.       57269
Ms.        38955
Mr.        10648
Teacher     2360
Dr.           13
Name: teacher_prefix, dtype: int64

In [9]:
# check if we have any nan values are there
print(project_data['teacher_prefix'].isnull().values.any())
print("number of nan values",project_data['teacher_prefix'].isnull().values.sum())

True
number of nan values 3


>numebr of missing values are very less in number, we can replace it with Mrs. as most of the projects are submitted by Mrs.

In [10]:
project_data['teacher_prefix']=project_data['teacher_prefix'].fillna('Mrs.')

In [11]:
project_data['teacher_prefix'].value_counts()

Mrs.       57272
Ms.        38955
Mr.        10648
Teacher     2360
Dr.           13
Name: teacher_prefix, dtype: int64

>Remove '.' <br>
>convert all the chars to small

In [12]:
project_data['teacher_prefix'] = project_data['teacher_prefix'].str.replace('.','').str.lower()
project_data['teacher_prefix'].value_counts()

mrs        57272
ms         38955
mr         10648
teacher     2360
dr            13
Name: teacher_prefix, dtype: int64

# 5. Preprocessing Categorical Features: project_subject_subcategories

In [13]:
project_data['project_subject_subcategories'].value_counts()

Literacy                                9486
Literacy, Mathematics                   8325
Literature & Writing, Mathematics       5923
Literacy, Literature & Writing          5571
Mathematics                             5379
                                        ... 
Other, Warmth, Care & Hunger               1
Gym & Fitness, Warmth, Care & Hunger       1
ESL, Team Sports                           1
Community Service, Music                   1
Economics, Nutrition Education             1
Name: project_subject_subcategories, Length: 401, dtype: int64

> same process we did in project_subject_categories

In [14]:
project_data['project_subject_subcategories'] = project_data['project_subject_subcategories']\
.str.replace(' The ','').str.replace(' ','').str.replace('&','_').str.replace(',','_').str.lower()

project_data['project_subject_subcategories'].value_counts()

literacy                                 9486
literacy_mathematics                     8325
literature_writing_mathematics           5923
literacy_literature_writing              5571
mathematics                              5379
                                         ... 
other_warmth_care_hunger                    1
extracurricular_financialliteracy           1
esl_teamsports                              1
literature_writing_nutritioneducation       1
economics_foreignlanguages                  1
Name: project_subject_subcategories, Length: 401, dtype: int64

# 6. Preprocessing Categorical Features: school_state

In [15]:
project_data['school_state'].value_counts()

CA    15388
TX     7396
NY     7318
FL     6185
NC     5091
IL     4350
GA     3963
SC     3936
MI     3161
PA     3109
IN     2620
MO     2576
OH     2467
LA     2394
MA     2389
WA     2334
OK     2276
NJ     2237
AZ     2147
VA     2045
WI     1827
AL     1762
UT     1731
TN     1688
CT     1663
MD     1514
NV     1367
MS     1323
KY     1304
OR     1242
MN     1208
CO     1111
AR     1049
ID      693
IA      666
KS      634
NM      557
DC      516
HI      507
ME      505
WV      503
NH      348
AK      345
DE      343
NE      309
SD      300
RI      285
MT      245
ND      143
WY       98
VT       80
Name: school_state, dtype: int64

>convert all of them into small letters

In [16]:
project_data['school_state'] = project_data['school_state'].str.lower()
project_data['school_state'].value_counts()

ca    15388
tx     7396
ny     7318
fl     6185
nc     5091
il     4350
ga     3963
sc     3936
mi     3161
pa     3109
in     2620
mo     2576
oh     2467
la     2394
ma     2389
wa     2334
ok     2276
nj     2237
az     2147
va     2045
wi     1827
al     1762
ut     1731
tn     1688
ct     1663
md     1514
nv     1367
ms     1323
ky     1304
or     1242
mn     1208
co     1111
ar     1049
id      693
ia      666
ks      634
nm      557
dc      516
hi      507
me      505
wv      503
nh      348
ak      345
de      343
ne      309
sd      300
ri      285
mt      245
nd      143
wy       98
vt       80
Name: school_state, dtype: int64

# 7. Preprocessing Categorical Features: project_title

In [17]:
# https://stackoverflow.com/a/47091490/4084039
import re

def decontracted(phrase):
    # specific
    phrase = re.sub(r"won't", "will not", phrase)
    phrase = re.sub(r"can\'t", "can not", phrase)

    # general
    phrase = re.sub(r"n\'t", " not", phrase)
    phrase = re.sub(r"\'re", " are", phrase)
    phrase = re.sub(r"\'s", " is", phrase)
    phrase = re.sub(r"\'d", " would", phrase)
    phrase = re.sub(r"\'ll", " will", phrase)
    phrase = re.sub(r"\'t", " not", phrase)
    phrase = re.sub(r"\'ve", " have", phrase)
    phrase = re.sub(r"\'m", " am", phrase)
    return phrase

In [18]:
# https://gist.github.com/sebleier/554280
# we are removing the words from the stop words list: 'no', 'nor', 'not'
stopwords= ['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've",\
            "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', \
            'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their',\
            'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', \
            'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', \
            'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', \
            'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after',\
            'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further',\
            'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more',\
            'most', 'other', 'some', 'such', 'only', 'own', 'same', 'so', 'than', 'too', 'very', \
            's', 't', 'can', 'will', 'just', 'don', "don't", 'should', "should've", 'now', 'd', 'll', 'm', 'o', 're', \
            've', 'y', 'ain', 'aren', "aren't", 'couldn', "couldn't", 'didn', "didn't", 'doesn', "doesn't", 'hadn',\
            "hadn't", 'hasn', "hasn't", 'haven', "haven't", 'isn', "isn't", 'ma', 'mightn', "mightn't", 'mustn',\
            "mustn't", 'needn', "needn't", 'shan', "shan't", 'shouldn', "shouldn't", 'wasn', "wasn't", 'weren', "weren't", \
            'won', "won't", 'wouldn', "wouldn't"]

In [19]:
project_data['project_title'].head(5)

0     Educational Support for English Learners at Home
1                Wanted: Projector for Hungry Learners
2    Soccer Equipment for AWESOME Middle School Stu...
3                               Techie Kindergarteners
4                               Interactive Math Tools
Name: project_title, dtype: object

In [20]:
print("printing some random reviews")
print(9, project_data['project_title'].values[9])
print(34, project_data['project_title'].values[34])
print(147, project_data['project_title'].values[147])

printing some random reviews
9 Just For the Love of Reading--\r\nPure Pleasure
34 \"Have A Ball!!!\"
147 Who needs a Chromebook?\r\nWE DO!!


In [21]:
# Combining all the above stundents 
from tqdm import tqdm
def preprocess_text(text_data):
    preprocessed_text = []
    # tqdm is for printing the status bar
    for sentance in tqdm(text_data):
        sent = decontracted(sentance)
        sent = sent.replace('\\r', ' ')
        sent = sent.replace('\\n', ' ')
        sent = sent.replace('\\"', ' ')
        sent = re.sub('[^A-Za-z0-9]+', ' ', sent)
        # https://gist.github.com/sebleier/554280
        sent = ' '.join(e for e in sent.split() if e.lower() not in stopwords)
        preprocessed_text.append(sent.lower().strip())
    return preprocessed_text

In [22]:
preprocessed_titles = preprocess_text(project_data['project_title'].values)

100%|███████████████████████████████████████████████████████████████████████| 109248/109248 [00:04<00:00, 23041.89it/s]


In [23]:
print("printing some random reviews")
print(9, preprocessed_titles[9])
print(34, preprocessed_titles[34])
print(147, preprocessed_titles[147])

printing some random reviews
9 love reading pure pleasure
34 ball
147 needs chromebook


# 8. Preprocessing Text Features: essay

In [24]:
# merge two column text dataframe: 
project_data["essay"] = project_data["project_essay_1"].map(str) + project_data["project_essay_2"].map(str) + \
                        project_data["project_essay_3"].map(str) + project_data["project_essay_4"].map(str)

In [25]:
print("printing some random essay")
print(9, project_data['essay'].values[9])
print('-'*50)
print(34, project_data['essay'].values[34])
print('-'*50)
print(147, project_data['essay'].values[147])

printing some random essay
9 Over 95% of my students are on free or reduced lunch.  I have a few who are homeless, but despite that, they come to school with an eagerness to learn.  My students are inquisitive eager learners who  embrace the challenge of not having great books and other resources  every day.  Many of them are not afforded the opportunity to engage with these big colorful pages of a book on a regular basis at home and they don't travel to the public library.  \r\nIt is my duty as a teacher to do all I can to provide each student an opportunity to succeed in every aspect of life. \r\nReading is Fundamental! My students will read these books over and over again while boosting their comprehension skills. These books will be used for read alouds, partner reading and for Independent reading. \r\nThey will engage in reading to build their \"Love for Reading\" by reading for pure enjoyment. They will be introduced to some new authors as well as some old favorites. I want my st

In [26]:
preprocessed_essays = preprocess_text(project_data['essay'].values)

100%|████████████████████████████████████████████████████████████████████████| 109248/109248 [01:27<00:00, 1241.95it/s]


In [27]:
print("printing some random essay")
print(9, preprocessed_essays[9])
print('-'*50)
print(34, preprocessed_essays[34])
print('-'*50)
print(147, preprocessed_essays[147])

printing some random essay
9 95 students free reduced lunch homeless despite come school eagerness learn students inquisitive eager learners embrace challenge not great books resources every day many not afforded opportunity engage big colorful pages book regular basis home not travel public library duty teacher provide student opportunity succeed every aspect life reading fundamental students read books boosting comprehension skills books used read alouds partner reading independent reading engage reading build love reading reading pure enjoyment introduced new authors well old favorites want students ready 21st century know pleasure holding good hard back book hand nothing like good book read students soar reading consideration generous funding contribution help build stamina prepare 3rd grade thank much reading proposal nannan
--------------------------------------------------
34 students mainly come extremely low income families majority come homes parents work full time students s

# 8. Preprocessing Numerical Values: price

In [28]:
# https://stackoverflow.com/questions/22407798/how-to-reset-a-dataframes-indexes-for-all-groups-in-one-step
price_data = resource_data.groupby('id').agg({'price':'sum', 'quantity':'sum'}).reset_index()
price_data.head(2)

id   price  quantity
0  p000001  459.56         7
1  p000002  515.89        21

In [29]:
# join two dataframes in python: 
project_data = pd.merge(project_data, price_data, on='id', how='left')

In [30]:
project_data.head(2)

Unnamed: 0       id                        teacher_id teacher_prefix  \
0      160221  p253737  c90749f5d961ff158d4b4d1e7dc665fc            mrs   
1      140945  p258326  897464ce9ddc600bced1151f324dd63a             mr   

  school_state project_submitted_datetime project_grade_category  \
0           in        2016-12-05 13:43:57          grades_prek_2   
1           fl        2016-10-25 09:22:10             grades_6_8   

     project_subject_categories project_subject_subcategories  \
0             literacy_language                  esl_literacy   
1  history_civics_health_sports  civics_government_teamsports   

                                      project_title  \
0  Educational Support for English Learners at Home   
1             Wanted: Projector for Hungry Learners   

                                     project_essay_1  \
0  My students are English learners that are work...   
1  Our students arrive to our school eager to lea...   

                                     project_essay_2 project_essay_3  \
0  \"The limits of your language are the limits o...             NaN   
1  The projector we need for our school is very c...             NaN   

  project_essay_4                           project_resource_summary  \
0             NaN  My students need opportunities to practice beg...   
1             NaN  My students need a projector to help with view...   

   teacher_number_of_previously_posted_projects  project_is_approved  \
0                                             0                    0   
1                                             7                    1   

                                               essay  price  quantity  
0  My students are English learners that are work...  154.6        23  
1  Our students arrive to our school eager to lea...  299.0         1

## 8.1 applying StandardScaler

In [31]:
# from sklearn.preprocessing import StandardScaler

# scaler = StandardScaler()
# scaler.fit(project_data['price'].values.reshape(-1, 1))
# project_data['std_price'] = scaler.transform(project_data['price'].values.reshape(-1, 1) )

In [32]:
# project_data['std_price'].head()

## 8.2 applying MinMaxScaler

In [33]:
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
scaler.fit(project_data['price'].values.reshape(-1, 1))
project_data['nrm_price']=scaler.transform(project_data['price'].values.reshape(-1, 1))

In [34]:
project_data['nrm_price'].head()

0    0.015397
1    0.029839
2    0.051628
3    0.023228
4    0.006733
Name: nrm_price, dtype: float64

In [35]:
scaler.fit(project_data['quantity'].values.reshape(-1, 1))
project_data['nrm_quantity']=scaler.transform(project_data['quantity'].values.reshape(-1, 1))

In [36]:
scaler.fit(project_data['teacher_number_of_previously_posted_projects'].values.reshape(-1, 1))
project_data['nrm_teacher_number_of_previously_posted_projects']=scaler.transform(project_data['teacher_number_of_previously_posted_projects'].values.reshape(-1, 1))

In [37]:
project_data.head(2)

Unnamed: 0       id                        teacher_id teacher_prefix  \
0      160221  p253737  c90749f5d961ff158d4b4d1e7dc665fc            mrs   
1      140945  p258326  897464ce9ddc600bced1151f324dd63a             mr   

  school_state project_submitted_datetime project_grade_category  \
0           in        2016-12-05 13:43:57          grades_prek_2   
1           fl        2016-10-25 09:22:10             grades_6_8   

     project_subject_categories project_subject_subcategories  \
0             literacy_language                  esl_literacy   
1  history_civics_health_sports  civics_government_teamsports   

                                      project_title  ... project_essay_4  \
0  Educational Support for English Learners at Home  ...             NaN   
1             Wanted: Projector for Hungry Learners  ...             NaN   

                            project_resource_summary  \
0  My students need opportunities to practice beg...   
1  My students need a projector to help with view...   

  teacher_number_of_previously_posted_projects project_is_approved  \
0                                            0                   0   
1                                            7                   1   

                                               essay  price  quantity  \
0  My students are English learners that are work...  154.6        23   
1  Our students arrive to our school eager to lea...  299.0         1   

  nrm_price  nrm_quantity  nrm_teacher_number_of_previously_posted_projects  
0  0.015397      0.023681                                          0.000000  
1  0.029839      0.000000                                          0.015521  

[2 rows x 23 columns]

In [38]:
for i in project_data.columns:
    print(i)

Unnamed: 0
id
teacher_id
teacher_prefix
school_state
project_submitted_datetime
project_grade_category
project_subject_categories
project_subject_subcategories
project_title
project_essay_1
project_essay_2
project_essay_3
project_essay_4
project_resource_summary
teacher_number_of_previously_posted_projects
project_is_approved
essay
price
quantity
nrm_price
nrm_quantity
nrm_teacher_number_of_previously_posted_projects


In [39]:
# project_data[['teacher_prefix', 'school_state', 'project_grade_category', 'project_subject_categories',
#               'project_subject_subcategories', 'project_title', 'project_resource_summary',
#               'nrm_teacher_number_of_previously_posted_projects', 'project_is_approved', 'essay', 'nrm_quantity', 'nrm_price']].to_csv('preprocessed_data_26.csv', index=False)

In [40]:
for index in project_data.index:
    print(project_data.loc[index, 'project_subject_subcategories'], '\n')

esl_literacy 

civics_government_teamsports 

health_wellness_teamsports 

literacy_mathematics 

mathematics 

literature_writing_specialneeds 

literacy_specialneeds 

mathematics 

health_wellness 

literacy_literature_writing 

literacy 

literacy_parentinvolvement 

environmentalscience_health_lifescience 

specialneeds 

literacy 

health_wellness 

literacy_specialneeds 

appliedsciences_literature_writing 

earlydevelopment 

health_wellness 

literacy 

health_lifescience_specialneeds 

literacy 

music 

appliedsciences_mathematics 

mathematics 

literacy_mathematics 

foreignlanguages_mathematics 

literacy_specialneeds 

literacy_other 

literacy 

specialneeds 

health_lifescience_literacy 

economics_financialliteracy 

literature_writing 

teamsports 

literature_writing_mathematics 

health_wellness_literacy 

gym_fitness_health_wellness 

literacy_literature_writing 

literacy_literature_writing 

literature_writing 

literacy_literature_writing 

literacy_visualarts 


mathematics 

music_parentinvolvement 

college_careerprep_earlydevelopment 

literacy 

mathematics 

specialneeds 

literacy_literature_writing 

gym_fitness_nutritioneducation 

music_performingarts 

health_wellness_specialneeds 

music 

visualarts 

esl_literacy 

gym_fitness_teamsports 

appliedsciences_parentinvolvement 

warmth_care_hunger 

other 

warmth_care_hunger 

literacy_literature_writing 

appliedsciences 

literacy_literature_writing 

earlydevelopment_literacy 

literacy 

appliedsciences_literature_writing 

literacy_mathematics 

literacy_mathematics 

health_wellness_teamsports 

literacy 

college_careerprep_other 

visualarts 

literacy 

literacy_literature_writing 

literature_writing_mathematics 

history_geography_literature_writing 

appliedsciences_mathematics 

literacy 

literature_writing_specialneeds 

music 

literature_writing_mathematics 

music 

literacy_mathematics 

music_performingarts 

appliedsciences_environmentalscience 

literature_writ

financialliteracy 

mathematics_specialneeds 

specialneeds 

appliedsciences_mathematics 

literature_writing_specialneeds 

literacy 

mathematics_socialsciences 

literature_writing 

appliedsciences_environmentalscience 

literacy 

environmentalscience_health_lifescience 

literacy_mathematics 

literacy_literature_writing 

literacy_literature_writing 

environmentalscience 

appliedsciences_environmentalscience 

literacy_literature_writing 

gym_fitness_teamsports 

college_careerprep_literature_writing 

literature_writing_mathematics 

appliedsciences_literacy 

nutritioneducation 

specialneeds_visualarts 

health_wellness 

appliedsciences 

other 

environmentalscience_mathematics 

earlydevelopment_specialneeds 

literature_writing 

literacy_mathematics 

literacy 

college_careerprep 

literacy_literature_writing 

appliedsciences 

gym_fitness_health_wellness 

health_wellness_specialneeds 

health_lifescience 

gym_fitness_teamsports 

socialsciences 

mathematics 

l


teamsports 

health_lifescience_health_wellness 

environmentalscience_mathematics 

environmentalscience_mathematics 

literacy_mathematics 

specialneeds 

mathematics 

gym_fitness 

music 

environmentalscience_health_lifescience 

literacy 

gym_fitness_performingarts 

health_wellness 

health_lifescience_mathematics 

music 

earlydevelopment_performingarts 

esl_literature_writing 

literacy 

literacy_literature_writing 

mathematics 

specialneeds 

literacy 

performingarts 

literature_writing 

health_wellness 

appliedsciences_environmentalscience 

literacy_specialneeds 

health_wellness_literacy 

literacy 

literacy_literature_writing 

literature_writing_mathematics 

environmentalscience 

other_visualarts 

health_wellness 

health_lifescience_other 

literature_writing_mathematics 

literacy_specialneeds 

literacy_mathematics 

literacy_literature_writing 

literature_writing_mathematics 

environmentalscience_extracurricular 

earlydevelopment_specialneeds 

ear


environmentalscience 

environmentalscience 

literacy 

mathematics 

health_wellness 

health_wellness_specialneeds 

environmentalscience_health_lifescience 

literacy_mathematics 

charactereducation_college_careerprep 

literacy 

civics_government_literacy 

literacy_other 

literature_writing_mathematics 

literacy_mathematics 

health_wellness_specialneeds 

environmentalscience_health_lifescience 

mathematics_other 

socialsciences 

literacy_literature_writing 

specialneeds 

history_geography 

warmth_care_hunger 

literacy 

appliedsciences_health_lifescience 

literature_writing_mathematics 

literature_writing_mathematics 

literacy 

history_geography_literature_writing 

earlydevelopment_mathematics 

literature_writing 

specialneeds 

health_wellness_literature_writing 

specialneeds 

mathematics_visualarts 

esl_literacy 

literature_writing_mathematics 

health_wellness 

literature_writing 

specialneeds 

literature_writing_mathematics 

literacy_mathematics 


...

literacy_mathematics 

appliedsciences_earlydevelopment 

civics_government_history_geography 

literature_writing_mathematics 

health_wellness 

appliedsciences_visualarts 

appliedsciences_literacy 

health_lifescience 

environmentalscience_health_lifescience 

literacy_specialneeds 

mathematics 

literature_writing 

earlydevelopment_health_wellness 

literature_writing 

earlydevelopment_specialneeds 

college_careerprep_literacy 

literacy_specialneeds 

literacy_literature_writing 

college_careerprep_literature_writing 

environmentalscience_specialneeds 

visualarts 

health_wellness_specialneeds 

literature_writing 

appliedsciences_mathematics 

literacy_mathematics 

gym_fitness_health_wellness 

health_wellness_specialneeds 

specialneeds 

mathematics 

literacy 

music 

mathematics_specialneeds 

literature_writing_mathematics 

literacy_mathematics 

literacy_mathematics 

college_careerprep 

literacy_socialsciences 

literature_writing_music 

appliedsciences_math


literacy_literature_writing 

literature_writing_visualarts 

literacy 

specialneeds_visualarts 

mathematics 

literacy_mathematics 

literature_writing_mathematics 

appliedsciences_mathematics 

literacy_mathematics 

health_wellness_specialneeds 

gym_fitness_health_wellness 

literacy_visualarts 

mathematics 

appliedsciences 

appliedsciences_literacy 

mathematics_specialneeds 

literacy_mathematics 

literacy 

esl_literacy 

literacy 

literacy_specialneeds 

visualarts 

music_visualarts 

health_wellness_teamsports 

literacy_literature_writing 

literature_writing 

gym_fitness_specialneeds 

mathematics 

appliedsciences_mathematics 

literature_writing_mathematics 

appliedsciences 

gym_fitness_teamsports 

specialneeds 

gym_fitness_health_wellness 

visualarts 

environmentalscience_health_lifescience 

appliedsciences_earlydevelopment 

literacy_mathematics 

literature_writing_socialsciences 

visualarts 

mathematics 

literacy_literature_writing 

health_wellnes

literacy_specialneeds 

specialneeds 

earlydevelopment_health_wellness 

literacy_literature_writing 

literacy 

literacy_literature_writing 

mathematics_specialneeds 

appliedsciences 

appliedsciences_mathematics 

health_wellness 

literacy_literature_writing 

appliedsciences_mathematics 

charactereducation_other 

specialneeds 

literature_writing_other 

environmentalscience 

literature_writing 

literacy_mathematics 

health_wellness_specialneeds 

visualarts 

music 

literacy_mathematics 

esl_literacy 

health_wellness 

appliedsciences 

specialneeds_visualarts 

foreignlanguages_literacy 

literacy_literature_writing 

gym_fitness_health_wellness 

literacy_mathematics 

mathematics 

gym_fitness_teamsports 

literacy_visualarts 

warmth_care_hunger 

literacy_mathematics 

charactereducation_literacy 

esl_mathematics 

literature_writing 

literacy_visualarts 

esl_literature_writing 

health_lifescience_mathematics 

foreignlanguages_mathematics 

literacy_mathemati


appliedsciences_literature_writing 

literacy_visualarts 

charactereducation_mathematics 

environmentalscience_visualarts 

environmentalscience 

earlydevelopment_specialneeds 

appliedsciences_mathematics 

appliedsciences_mathematics 

literature_writing_socialsciences 

literacy_literature_writing 

health_lifescience_literature_writing 

history_geography_literacy 

esl_health_wellness 

specialneeds 

health_lifescience_literacy 

appliedsciences_mathematics 

literature_writing_mathematics 

college_careerprep_visualarts 

specialneeds 

literacy 

extracurricular 

college_careerprep 

music_visualarts 

earlydevelopment_mathematics 

gym_fitness_health_wellness 

health_wellness 

literacy_mathematics 

appliedsciences_mathematics 

literature_writing 

literacy 

esl_literacy 

literacy 

esl_literacy 

specialneeds_visualarts 

literature_writing 

literacy_mathematics 

literacy_mathematics 

specialneeds 

health_lifescience_literacy 

literacy 

teamsports 

esl_social

foreignlanguages_literacy 

health_wellness 

literacy_mathematics 

literacy 

earlydevelopment_literacy 

appliedsciences_literacy 

literature_writing_mathematics 

literacy_mathematics 

literacy_mathematics 

health_wellness_specialneeds 

college_careerprep_mathematics 



In [41]:
project_data.loc[74826, 'project_subject_subcategories']

'literacy'